# [Diophantine Equation](https://projecteuler.net/problem=66)

SageMath can solve these [Diophantine equations](https://en.wikipedia.org/wiki/Diophantine_equation) for us. For equations of the form $x^2 - Dy^2 = 1$ (which are called [Pell equations](https://en.wikipedia.org/wiki/Pell%27s_equation)), it will give parameterizations in $t$ for both $x$ and $y$. Here's $D=2$ as an example:

In [1]:
var('x,y')
solve_diophantine(x^2 - 2*y^2 == 1)

[(-sqrt(2)*(2*sqrt(2) + 3)^t + sqrt(2)*(-2*sqrt(2) + 3)^t - 3/2*(2*sqrt(2) + 3)^t - 3/2*(-2*sqrt(2) + 3)^t,
  3/4*sqrt(2)*(2*sqrt(2) + 3)^t - 3/4*sqrt(2)*(-2*sqrt(2) + 3)^t + (2*sqrt(2) + 3)^t + (-2*sqrt(2) + 3)^t),
 (sqrt(2)*(2*sqrt(2) + 3)^t - sqrt(2)*(-2*sqrt(2) + 3)^t + 3/2*(2*sqrt(2) + 3)^t + 3/2*(-2*sqrt(2) + 3)^t,
  -3/4*sqrt(2)*(2*sqrt(2) + 3)^t + 3/4*sqrt(2)*(-2*sqrt(2) + 3)^t - (2*sqrt(2) + 3)^t - (-2*sqrt(2) + 3)^t)]

$t=0$ seems to correspond to the minimal solution we are after.

In [2]:
def minimal_solution(d):
    var('x,y')
    
    sols = solve_diophantine(x^2 - d*y^2 == 1)
    u, v = sols[0]
    return (abs(u(t=0).simplify_full()), abs(v(t=0).simplify_full()))

Now we can just iterate (although it is pretty slow).

In [3]:
max((d for d in range(1, 1001) if not is_square(d)), key=lambda k: minimal_solution(k)[0])

661

Let's dig a little deeper so we can optimize.

## Solving Pell equations
Lagrange proved that if $(x_0, y_0)$ is a solution to
$$x^2 - dy^2 = 1$$
then $\frac{x_0}{y_0}$ is a [convergent of the continued fraction](https://en.wikipedia.org/wiki/Simple_continued_fraction) of $\sqrt{d}$. This is great for us, since we can write generators for computing convergents of square roots (FYI, SageMath can do this with built-in methods: `continued_fraction(sqrt(d)).convergents()`).

In [4]:
def continued_fraction_sqrt(d):
    x = sqrt(d)
    while True:
        b = floor(x)
        yield b
        x = (x - b)^-1
        
        
def convergents(partial_denoms):
    h, hprev = 1, 0
    k, kprev = 0, 1
    for b in partial_denoms:
        h, hprev = b * h + hprev, h
        k, kprev = b * k + kprev, k
        yield h/k

Then we can just iterate over each convergent to see if its numerator and denominator are a solution to the Pell equation.

In [5]:
def pell_fundamental_solution(d):
    partial_denoms = continued_fraction_sqrt(d)
    for f in convergents(partial_denoms):
        x, y = f.as_integer_ratio()
        if x^2 - d*y^2 == 1:
            return (x, y)

Now we'll just iterate with this function instead.

In [6]:
max((d for d in range(1, 1001) if not is_square(d)), key=lambda x: pell_fundamental_solution(x)[0])

661

## Relevant sequences
* Minimal values of $x$ for solutions to the Pell equation: [A002350](https://oeis.org/A002350)